In [111]:
import os
import re
earlygreekepic = ['tlg0012','tlg0020','tlg0013']

def addentry(curdict,curitem):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1

def getepicfiles():
    rlist = []
    for (root,dirs,files) in os.walk('.'):
        m = re.search('(tlg[0-9]+)',root)
        if(not m):
            continue
        if(m and not m[1] in earlygreekepic):
            continue
        for file in files:
            if(re.search('tlg0012.tlg00[12].daphne_tb',file)):
                continue
            if(re.search('tlg0020.tlg00[123].daphne_tb',file)):
                continue
            if(re.search('\.bak',file)):
                continue
            if(re.search('conllu$',file)):
                #print(root,file)
                rlist.append(root+'/'+file)
    return(rlist)

flist = getepicfiles()
flist

['./tlg0020/tlg0020.tlg002.daphne_perstb-grc1.conllu',
 './tlg0020/tlg0020.tlg003.daphne_perstb-grc1.conllu',
 './tlg0020/tlg0020.tlg001.daphne_perstb-grc1.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.1-6.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.7-12.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.13-18.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.19-24.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.7-12.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.19-24.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.1-6.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.13-18.conllu',
 './tlg0013/tlg0013.tlg002.daphne_tb-grc1.conllu']

In [112]:
wordid2cit = {}
wordid2form= {}
wordid2lemma = {}
wordid2upos = {}
wordid2xpos = {}
wordid2feats = {}
wordid2head = {}
wordid2deprel = {}
wordid2deplist = {}
lemmaindex = {}
verbargs = {}
worddeprels = {}


def additem(curdict,curitem):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1

def add2lemmaindex(lemmaindex,lemma,wordid):
    if(not lemma in lemmaindex):
        lemmaindex[lemma] = [wordid]
    else:
        lemmaindex[lemma].append(wordid)

def loadUDfile(fname):
    cursentid = ''
    m = re.search('(tlg[0-9]+\.tlg[0-9]+)',fname)
    if(not m):
        print(fname,'expected file name with tlg[0-9]+\.tlg[0-9]+')
        return

    else:
        curtgwork = m[1]
    f = open(fname)
    for l in f:
        l = re.sub('\s+$','',l)
        if(re.search('u--------',l)):
            continue
        curcit = ''
        m = re.search('sent_id\s*=\s*([0-9a-b]+)',l)
        if(m):
            cursentid = m[1]
        m = re.search('^([0-9]+)\s',l)
        if(not m):
            continue
        args = l.split()
            
        wordid = curtgwork + ':sent-' + cursentid + ':' + m[1]
        m = re.search('Ref=([^\|]+)',l)
        if(m):
            curcit = curtgwork + ':' + m[1]
        wordid2cit[wordid] = curcit
        args = l.split()
        #print(len(args),l)
        wordid2form[wordid] = args[1]
        wordid2lemma[wordid] = args[2]
        add2lemmaindex(lemmaindex,args[2],wordid)
        wordid2upos[wordid] = args[3]
        wordid2xpos[wordid] = args[4]
        wordid2feats[wordid] = args[5]
        wordid2head[wordid] = curtgwork + ':sent-' + cursentid + ':' + args[6]
            
        wordid2deprel[wordid] = args[7]
    f.close()

saveconjs = {}
def resolveconj():
    for wordid in wordid2deprel:
        if(wordid2lemma[wordid] == 'μῆνις'):
            print('1',wordid)
        #print('2',wordid,wordid2lemma[wordid])
        if(wordid2deprel[wordid] == 'conj'):
            curlemma = wordid2lemma[wordid]
            if(not curlemma in saveconjs):
                saveconjs[curlemma] = {}
            additem(saveconjs[curlemma],wordid+':'+wordid2lemma[wordid] + ':' + wordid2head[wordid] + ':'  + wordid2lemma[wordid2head[wordid]])
            wordid2deprel[wordid] = wordid2deprel[wordid2head[wordid]]
            wordid2head[wordid] = wordid2head[wordid2head[wordid]]
        if(not wordid2head[wordid] in wordid2deplist):
            wordid2deplist[wordid2head[wordid]] = [wordid]
        else:
            wordid2deplist[wordid2head[wordid]].append(wordid)
        if(not wordid in wordid2lemma):
            print('missing lemma',wordid)
            continue
        if(not wordid2lemma[wordid] in worddeprels):
            worddeprels[wordid2lemma[wordid]] = {}
        if(wordid2lemma[wordid] == 'μῆνις'):
            print(wordid,wordid2lemma[wordid],worddeprels[wordid2lemma[wordid]])
        additem(worddeprels[wordid2lemma[wordid]],wordid2deprel[wordid])

        
        


lemmadeps = {}
def getdeps(lemma):
    rlist = {}
    if(not lemma in lemmaindex):
        return

    print(lemma,len(lemmaindex[lemma]))
    for wordid in lemmaindex[lemma]:
        if(not wordid in wordid2deplist):
            continue
        print('\n'+wordid,wordid2lemma[wordid],wordid2form[wordid])
        for depid in wordid2deplist[wordid]:
            if(not lemma in verbargs):
                verbargs[lemma] = {}
            
            additem(verbargs[lemma],wordid2lemma[depid]+ ':' + wordid2deprel[depid])
            print(depid,wordid2form[depid],wordid2lemma[depid],wordid2deprel[depid])
            
            
for fname in flist:   
    loadUDfile(fname)
resolveconj()




curlemma = 'συνάγω'
getdeps(curlemma)
for foo in sorted(verbargs[curlemma],key=verbargs[curlemma].get,reverse=True):
    print(foo,verbargs[curlemma][foo])


1 tlg0020.tlg003:sent-2273422:5
tlg0020.tlg003:sent-2273422:5 μῆνις {}
1 tlg0012.tlg001:sent-2274106:1
tlg0012.tlg001:sent-2274106:1 μῆνις {'obj': 1}
1 tlg0012.tlg001:sent-2274140:8
tlg0012.tlg001:sent-2274140:8 μῆνις {'obj': 2}
1 tlg0012.tlg001:sent-2275445:29
tlg0012.tlg001:sent-2275445:29 μῆνις {'obj': 3}
1 tlg0012.tlg001:sent-2275520:5
tlg0012.tlg001:sent-2275520:5 μῆνις {'obj': 4}
1 tlg0012.tlg001:sent-2275665:9
tlg0012.tlg001:sent-2275665:9 μῆνις {'obj': 4, 'nsubj': 1}
1 tlg0012.tlg001:sent-2277013:22
tlg0012.tlg001:sent-2277013:22 μῆνις {'obj': 5, 'nsubj': 1}
1 tlg0012.tlg001:sent-2278452:35
tlg0012.tlg001:sent-2278452:35 μῆνις {'obj': 6, 'nsubj': 1}
1 tlg0012.tlg001:sent-2278897:14
tlg0012.tlg001:sent-2278897:14 μῆνις {'obj': 7, 'nsubj': 1}
1 tlg0012.tlg001:sent-2279597:9
tlg0012.tlg001:sent-2279597:9 μῆνις {'obj': 7, 'nsubj': 1, 'amod': 1}
1 tlg0012.tlg001:sent-2280451:9
tlg0012.tlg001:sent-2280451:9 μῆνις {'obj': 8, 'nsubj': 1, 'amod': 1}
1 tlg0012.tlg001:sent-2280470:9
tlg00

In [113]:
saveconjs

{'φατός': {'tlg0020.tlg002:sent-1715892:8:φατός:tlg0020.tlg002:sent-1715892:6:ἄφατος': 1,
  'tlg0020.tlg003:sent-2273530:10:φατός:tlg0020.tlg003:sent-2273530:6:ἄπλατος': 1},
 'ῥητός': {'tlg0020.tlg002:sent-1715892:11:ῥητός:tlg0020.tlg002:sent-1715892:6:ἄφατος': 1},
 'ἄρρητος': {'tlg0020.tlg002:sent-1715892:13:ἄρρητος:tlg0020.tlg002:sent-1715892:11:ῥητός': 1},
 'χαλέπτω': {'tlg0020.tlg002:sent-1715893:9:χαλέπτω:tlg0020.tlg002:sent-1715893:4:βριάω': 1},
 'μινύθω': {'tlg0020.tlg002:sent-1715893:14:μινύθω:tlg0020.tlg002:sent-1715893:4:βριάω': 1,
  'tlg0020.tlg002:sent-1716038:5:μινύθω:tlg0020.tlg002:sent-1716038:3:τίκτω': 1,
  'tlg0020.tlg002:sent-1716081:7:μινύθω:tlg0020.tlg002:sent-1716081:4:μαυρόω': 1,
  'tlg0020.tlg002:sent-1716131:47:μινύθω:tlg0020.tlg002:sent-1716131:31:αἰτέω': 1,
  'tlg0012.tlg001:sent-2279082:17:μινύθω:tlg0012.tlg001:sent-2279082:13:ἐγγυαλίζω': 1,
  'tlg0012.tlg001:sent-2279427:28:μινύθω:tlg0012.tlg001:sent-2279427:7:πλήθω': 1,
  'tlg0012.tlg001:sent-2280067:19:μιν

In [101]:
lemmacounts = {}

for curlemma in lemmaindex:
    lemmacounts[curlemma] = len(lemmaindex[curlemma])

def getactiverbs():
    curvoice = ''
    curdeprel = ''
    for wordid in wordid2lemma:
        curlemma = wordid2lemma[wordid]
        m = re.search('Voice=(Act|MidPass|Mid|Pass)',wordid2feats[wordid])
        if(not m):
            continue
        curvoice = m[1]
        #print('feats',wordid,wordid2lemma[wordid],wordid2feats[wordid])
        if(not wordid in wordid2deplist):
            continue
        curobjs = []
        curcase = ''
        if(not curlemma in verbobjsindex):
            verbobjsindex[curlemma] = {}
        if(not wordid2lemma[wordid] in activeverbobjs):
            activeverbobjs[wordid2lemma[wordid]] = {}
        for wordid2 in wordid2deplist[wordid]:
            #print('feats',wordid,wordid2lemma[wordid],wordid2feats[wordid],wordid2,wordid2deprel[wordid2])
            m = re.search('\\b(obj|iobj|ccomp)',wordid2deprel[wordid2])
            if(m):
                curdeprel = m[1]
                m = re.search('Case=([A-Za-z]+)',wordid2feats[wordid2])
                if(m):
                    curcase = m[1]
                else:
                    curcase = 'nocase'
                curkey = curvoice + ':' + curdeprel + ':' + curcase + ':' + wordid2lemma[wordid2]
                
                if(not curkey in verbobjsindex[curlemma]):
                    verbobjsindex[curlemma][curkey] = [wordid + ':' + wordid2]
                else:
                    verbobjsindex[curlemma][curkey].append(wordid + ':' + wordid2)
                curobjs.append(wordid2)
                addentry(activeverbobjs[wordid2lemma[wordid]],curkey)
                #print('actobj',wordid,wordid2lemma[wordid],wordid2lemma[wordid2])
        if(not curobjs):
            curkey = curvoice+':'+'noobj'+':NA'
            curobjs.append(curkey)
            if(not curkey in verbobjsindex[curlemma]):
                verbobjsindex[curlemma][curkey] = [wordid + ':' + wordid2]
            else:
                verbobjsindex[curlemma][curkey].append(wordid + ':' + wordid2)
            addentry(activeverbobjs[wordid2lemma[wordid]],curvoice+':'+'noobj'+':NA')
            #print('noaccobj',wordid,wordid2lemma[wordid])
        #if(len(curobjs)>1):
         #   print('mult',len(curobjs),wordid,curobjs)

activeverbobjs = {}
verbobjsindex = {}
                
getactiverbs()
verbobjsindex

{'κλείω': {'Act:noobj:NA': ['tlg0020.tlg002:sent1715891:4:tlg0020.tlg002:sent1715891:3'],
  'Act:obj:Acc:εἰμί': ['tlg0020.tlg001:sent2273677:8:tlg0020.tlg001:sent2273677:11',
   'tlg0020.tlg001:sent2273677:8:tlg0020.tlg001:sent2273677:14'],
  'Act:obj:Acc:ἦθος': ['tlg0020.tlg001:sent2273692:15:tlg0020.tlg001:sent2273692:12'],
  'Act:obj:Acc:γένος': ['tlg0020.tlg001:sent2273712:1:tlg0020.tlg001:sent2273712:5'],
  'Act:obj:nocase:ὁ': ['tlg0012.tlg002:sent2185714:19:tlg0012.tlg002:sent2185714:17'],
  'Act:obj:Acc:σύ': ['tlg0012.tlg002:sent2190319:5:tlg0012.tlg002:sent2190319:4']},
 'ἐνέπω': {'Act:obj:Acc:Ζεύς': ['tlg0020.tlg002:sent1715891:8:tlg0020.tlg002:sent1715891:7'],
  'Act:obj:Dat:μῦθος': ['tlg0020.tlg002:sent1716001:10:tlg0020.tlg002:sent1716001:8'],
  'Act:noobj:NA': ['tlg0020.tlg002:sent1716045:35:tlg0020.tlg002:sent1716045:34',
   'tlg0012.tlg001:sent2277790:13:tlg0012.tlg001:sent2277790:12',
   'tlg0012.tlg002:sent2191971:14:tlg0012.tlg002:sent2191971:13',
   'tlg0012.tlg002:s

In [103]:
print(len(activeverbobjs))
for curlemma in sorted(lemmacounts,key=lemmacounts.get,reverse=True):
    if(not curlemma in activeverbobjs):
        continue
    curdict = activeverbobjs[curlemma]
    formcnt = 0
    for foo in curdict:
        formcnt = formcnt + curdict[foo]
    print('\nlemma:'+curlemma,lemmacounts[curlemma],len(curdict))
    for boo in sorted(curdict,key=curdict.get,reverse=True):
        print(boo,curdict[boo])
    
activeverbobjs

2542

lemma:εἰμί 2299 37
Act:noobj:NA 593
Mid:noobj:NA 52
Act:obj:Dat:ἐγώ 20
Act:obj:Dat:ἕ 10
Act:obj:Dat:σύ 8
MidPass:noobj:NA 7
Act:iobj:Dat:ἐγώ 4
Mid:obj:Dat:σύ 3
Pass:noobj:NA 3
Act:obj:Dat:ὅς 3
Act:obj:Gen:ἄλλος 2
Mid:obj:Dat:ὁ 2
Act:obj:Gen:θεός 2
Act:obj:Dat:πούς 2
Act:obj:Dat:Μενέλαος 1
Act:obj:Gen:ἄνθρωπος 1
Act:obj:Dat:Κουρῆτες 1
Act:obj:Acc:ἔργον 1
Act:obj:Acc:ὅς 1
Act:obj:nocase:κλισίηθεν 1
Act:obj:Gen:ἀνήρ 1
Act:obj:Dat:ὁ 1
Act:obj:Dat:Φαίαξ 1
Act:obj:Dat:εἰμί 1
Act:ccomp:nocase:ἔχω 1
Act:ccomp:nocase:ἀκουάζομαι 1
Act:ccomp:nocase:φορέω 1
Act:ccomp:nocase:ἐγχέω 1
Act:obj:Acc:φάος:φόως 1
Act:obj:Dat:αὐτός 1
Act:obj:Acc:νόος 1
Act:obj:Gen:βροτός 1
Act:obj:Gen:Ἄργος 1
Act:obj:nocase:ἐνθάδε 1
Act:obj:Gen:πόλις 1
Act:obj:nocase:ξυνεείκοσι 1
Act:obj:Dat:βροτός 1

lemma:ἔχω 887 444
Act:noobj:NA 70
Act:obj:Acc:θυμός 34
Act:obj:Acc:δῶμα 25
Act:obj:Acc:ἵππος 24
Act:obj:Acc:ἔγχος 22
Act:obj:Acc:οὐρανός 22
Mid:noobj:NA 17
Act:obj:Acc:ἐγώ 16
Act:obj:Acc:Ὄλυμπος 15
Act:obj:Acc:τεῦχος 14

Act:obj:Dat:ἀδώτης 1
Act:obj:Acc:μέγας 1
Act:obj:Acc:ἄμαξα 1
Act:obj:Dat:γῆρας 1
Act:obj:Dat:βροτός 1
Act:obj:Acc:ὄπις 1
Act:obj:Acc:κεραυνός 1
Act:obj:Acc:στεροπή 1
Act:obj:Acc:κυμοπόλεια 1
Act:ccomp:nocase:ἐκπέρθω 1
Act:ccomp:nocase:ἱκνέομαι 1
Act:iobj:Dat:πατήρ 1
Act:obj:Acc:κόρη 1
Act:obj:nocase:πάλιν 1
Act:ccomp:nocase:ἐξαλαπάζω 1
Act:obj:Dat:Ζεύς 1
Act:obj:Dat:Ἀργειφόντης 1
Act:obj:Dat:Πέλοψ 1
Act:obj:Dat:Ἀτρεύς 1
Act:obj:Acc:θέμις 1
Act:iobj:Dat:ἵππος 1
Act:ccomp:nocase:δύω 1
Act:ccomp:nocase:τίνω 1
Act:obj:Acc:ἐπίκουρος 1
Act:iobj:Dat:Διομήδης 1
Act:ccomp:nocase:αἱρέω 1
Act:obj:Gen:ὅς 1
Act:iobj:Dat:Αἰνείας 1
MidPass:obj:Dat:σύ 1
Act:iobj:Dat:θεράπων 1
Act:obj:Acc:ἥμισυς 1
Act:ccomp:nocase:πίπτω 1
Act:ccomp:nocase:ἀνάσσω 1
Act:ccomp:nocase:ἵστημι 1
Act:iobj:Dat:ναύτης 1
Act:iobj:Dat:Δαναοί 1
Act:obj:Dat:Ἐρευθαλίων 1
Act:iobj:Dat:Αἴας 1
Act:obj:nocase:αἴρω 1
Act:obj:Acc:μέγεθος 1
Act:obj:Acc:βία 1
Act:iobj:Dat:ἀλλήλων 1
Act:obj:Acc:ἄλοχος 1
Act:obj:Acc:μέθυ 1
Act:obj:Acc:ἡνία 1


Act:iobj:Dat:βωμός 1
Mid:iobj:Dat:ὁ 1
Mid:obj:Acc:κότος 1
MidPass:obj:Acc:δόρπον 1
Act:obj:Acc:δαίς 1
Act:obj:Gen:αἴξ 1
Act:obj:Acc:κέλαδος 1
Act:obj:Acc:ἀυτή 1
Act:obj:Dat:κεφαλή 1
Act:obj:Dat:δέρμα 1
Act:obj:Gen:Κουρῆτες 1
Act:obj:Gen:Αἰτωλός 1
Mid:obj:Acc:θυμός 1
Mid:obj:Acc:στεφάνη 1
MidPass:iobj:Dat:ὦμος 1
MidPass:obj:Acc:ἔντεα 1
Act:obj:Acc:φρήν 1
Act:iobj:Dat:ἱερόν 1
Act:obj:Acc:τεῖχος 1
Act:iobj:Dat:γαῖα 1
Act:obj:Acc:κέλευθος 1
Act:obj:Acc:πούς 1
Mid:iobj:Dat:φρήν 1
Mid:obj:Acc:νέμεσις 1
Act:obj:Acc:δαίδαλος 1
Mid:iobj:Dat:χρώς 1
Mid:obj:Acc:κόσμος 1
Act:obj:Acc:παλίωξις 1
Act:obj:Acc:τέλος 1
Mid:obj:Acc:πόνος 1
Mid:obj:Acc:δῆρις 1
Act:obj:Acc:βουλή 1
Act:obj:Acc:βία 1
Act:iobj:Dat:ὦμος 1
Act:obj:Acc:ῥόος 1
Act:obj:Acc:κύκλος 1
Act:obj:Acc:φῦσα 1
Act:iobj:Dat:ἀκμόθετον 1
Act:obj:Acc:ἄκμων 1
Act:obj:Acc:νειός 1
Act:obj:Acc:τέμενος 1
Act:obj:Acc:ἀλωή 1
Act:obj:Acc:τεῦχος 1
Act:obj:Acc:ἔπος 1
Act:iobj:Dat:ἀγορά 1
Act:obj:Acc:δεῖπνον 1
Mid:obj:Acc:τρυφάλεια 1
Mid:iobj:Dat:κράς 1
A

Act:obj:Acc:κόρη 1
Act:obj:Acc:βροτός 1
MidPass:obj:Acc:ἦμαρ 1
Act:iobj:Dat:μέγαρον 1
Act:obj:Acc:παῖς 1
Act:obj:Acc:ἄνθρωπος 1
MidPass:obj:Acc:δῶμα 1
MidPass:obj:Acc:αὐτός 1
Act:obj:Acc:ναῦς 1
Act:obj:Acc:στέλλω 1
Act:obj:Acc:ἔχω 1
Mid:obj:Acc:ναῦς 1
MidPass:obj:Acc:ἐγώ 1
Act:obj:Acc:Ἑλένη 1
Mid:obj:Acc:ὅς 1
MidPass:obj:Acc:παῖς 1

lemma:μάχομαι 256 45
MidPass:noobj:NA 106
Mid:noobj:NA 24
MidPass:obj:Dat:Τρώς 10
MidPass:obj:Dat:ἀνήρ 7
Mid:obj:Dat:Τρώς 6
Mid:obj:Dat:ἀνήρ 5
MidPass:obj:Dat:θεός 5
MidPass:obj:Acc:μάχη 5
MidPass:obj:Dat:Ζεύς 4
Mid:obj:Dat:σύ 4
MidPass:obj:Dat:ἀθάνατος 3
Mid:obj:Dat:Δαναοί 3
MidPass:obj:Dat:Ἕκτωρ 3
MidPass:obj:Dat:ἕ 2
MidPass:obj:Dat:σύ 2
Mid:obj:Dat:ἐγώ 2
MidPass:obj:Dat:φώς 2
MidPass:obj:Dat:πατήρ 2
MidPass:obj:Dat:πλείων 2
MidPass:obj:Dat:ἐγώ 2
MidPass:obj:Dat:Τιτάν 1
MidPass:obj:Dat:ἀλλήλων 1
MidPass:obj:Dat:κράτιστος 1
MidPass:obj:Dat:ἐκεῖνος:κεῖνος 1
MidPass:obj:Dat:Ἑλένη 1
MidPass:obj:Dat:κτῆμα 1
MidPass:obj:Dat:δάϊος2:δάιος 1
MidPass:obj:Dat:ἀλυσκά

Act:obj:Acc:Ὀδυσσεύς 3
Act:obj:Acc:Ἰδομενεύς 2
Act:obj:Acc:Ἄρης 2
Act:iobj:Acc:ὁ 2
Act:obj:Acc:κασίγνητος 2
Act:obj:Acc:υἱός 2
Act:obj:Acc:Τηλέμαχος 2
Act:iobj:Acc:Εὔμαιος 2
Act:obj:Acc:μήτηρ 1
Act:obj:Acc:Ταλθύβιος 1
Act:iobj:Acc:Τυδεΐδης:Τυδείδης 1
Act:obj:Acc:Προῖτος 1
Act:obj:Acc:ποιμήν 1
Act:obj:Acc:βασιλεύς 1
Act:iobj:Acc:Ὀϊλιάδης 1
Act:iobj:Acc:Ἀσκληπιάδης 1
Act:iobj:Acc:Ἶρις 1
Act:obj:Acc:Αὐτομέδων 1
Act:obj:Acc:Ἀλκιμέδων 1
Act:iobj:Acc:μήτηρ 1
Act:iobj:Acc:Ἥρα 1
Act:obj:Acc:Πηλείων 1
Act:obj:Acc:σφεῖς 1
Act:obj:Acc:βουκόλος 1
Act:obj:Acc:συβώτης 1
Act:obj:Acc:ἀοιδός 1
Act:obj:Acc:Ἀθήνη 1
Act:obj:Acc:Ὀδυσσεύς:̓ὀδυσσεύς 1
Act:iobj:Acc:Ἀντίνοος 1
Act:obj:Acc:ὑφορβός 1
Act:obj:Acc:Πηνελόπεια 1

lemma:ἐλαύνω 181 66
Act:noobj:NA 47
Act:obj:Acc:ἵππος 22
Act:obj:Acc:χαλκός 9
Act:obj:Acc:μιν 8
MidPass:noobj:NA 7
Act:obj:Acc:ὁ 5
Act:obj:Acc:μῆλον1:μῆλον 5
Act:obj:Acc:αὐχήν 4
Act:obj:Acc:ἅρμα 4
Act:obj:Acc:βοῦς 4
Act:obj:Acc:ναῦς 4
Act:obj:Acc:τάφρος 3
Act:iobj:Dat:αὐτός 2
Act:obj:Acc:φά

...

Act:obj:Acc:ὁ 1
Act:obj:Acc:ἕκαστος 1
Act:obj:Dat:ἀλλήλων 1

lemma:διελαύνω 4 5
Act:obj:Acc:ἵππος 2
Act:obj:Gen:τάφρος 1
Act:obj:Acc:ἅρμα 1
Act:obj:Gen:ὁ 1
Act:obj:Gen:λαπάρα 1

lemma:ἡνιοχεύω 4 1
Act:noobj:NA 4

lemma:ῥαίνω 4 2
MidPass:obj:Dat:αἷμα 2
MidPass:obj:Dat:κόνιος 1

lemma:ἐγρήσσω 4 1
Act:noobj:NA 3

lemma:ἀποψύχω 4 3
MidPass:obj:Acc:ἱδρώς 2
MidPass:obj:Gen:χιτών 1
Pass:noobj:NA 1

lemma:δαιτρεύω 4 1
Act:noobj:NA 1

lemma:ἀμφίστημι 4 2
Act:noobj:NA 3
MidPass:noobj:NA 1

lemma:γεγωνέω 4 3
Act:obj:Dat:Κίκονες 1
Act:obj:Dat:θεός 1
Act:obj:Dat:Τηλέμαχος 1

lemma:εἰσάλλομαι 4 3
Mid:obj:Acc:τεῖχος 2
MidPass:obj:Acc:πύλη 2
MidPass:obj:Acc:τεῖχος 1

lemma:διαίνω 4 4
MidPass:noobj:NA 1
Act:obj:Acc:μιν 1
Act:obj:Acc:χεῖλος 1
Act:obj:Acc:ὑπερῴα 1

lemma:ψαύω 4 4
Act:obj:Dat:φάλος 1
Act:noobj:NA 1
Act:obj:Gen:ἐπίσωτρον 1
Act:obj:Gen:ἔνδινα 1

lemma:προτύπτω 4 1
Act:noobj:NA 4

lemma:ὁρμέω 4 1
Pass:noobj:NA 2

lemma:ὑπερπέτομαι 4 2
Mid:noobj:NA 3
Mid:obj:Acc:σῆμα 1

lemma:γάνυμαι 4 3
MidP

Act:noobj:NA 1

lemma:οὐρέω 2 1
Act:noobj:NA 2

lemma:ἀπογυμνόω 2 1
Pass:noobj:NA 1

lemma:μωμεύω 2 2
Act:obj:Acc:ἀίδηλος 1
Act:noobj:NA 1

lemma:ἐξαλέομαι 2 2
Mid:noobj:NA 1
Mid:obj:Acc:πέμπτος 1

lemma:ἐποπτεύω 2 1
Act:obj:Acc:ἔργον 2

lemma:πραύνω 2 6
Act:obj:Acc:μῆλον 1
Act:obj:Acc:βοῦς 1
Act:obj:Acc:κύων 1
Act:obj:Acc:ὀρεύς 1
Act:obj:Acc:κῦμα 1
Act:obj:Acc:πνοή 1

lemma:καταφλέγω 2 2
Act:obj:Acc:κώμη 1
Act:obj:Acc:ὅδε 1

lemma:ἀμφιδαίω 2 2
Act:obj:Acc:σφεῖς 1
Act:obj:Acc:ἄστυ 1

lemma:ἀμφαραβέω 2 1
Act:noobj:NA 2

lemma:ἀναστρωφάω 2 2
Act:obj:Acc:ἵππος 1
Act:noobj:NA 1

lemma:κιθαρίζω 2 1
Act:noobj:NA 2

lemma:θοινάω 2 1
MidPass:obj:Acc:ἰχθύς 1

lemma:ἐπιψαύω 2 2
Act:obj:Gen:σάκος 1
Act:noobj:NA 1

lemma:λιχμάζω 2 1
Act:noobj:NA 2

lemma:ἐρέικω 2 2
Act:obj:Acc:χθών 1
MidPass:noobj:NA 1

lemma:τραπέω 2 2
Act:noobj:NA 1
Act:obj:Acc:ἄλλος 1

lemma:προγίγνομαι 2 1
Mid:noobj:NA 2

lemma:χρεμετίζω 2 1
Act:noobj:NA 2

lemma:καναχίζω 2 1
Act:noobj:NA 2

lemma:αἰόλλω 2 2
MidPass:noobj:NA 1

lemma:πλάσσω 1 1
Act:obj:Acc:ἴκελος 1

lemma:ἐκπέτομαι 1 1
Act:noobj:NA 1

lemma:ἐπιλαμβάνω 1 1
Act:noobj:NA 1

lemma:ἐκκορυφόω 1 1
Act:obj:Acc:λόγος 1

lemma:μέμφομαι 1 1
Mid:obj:Acc:ὁ 1

lemma:στέρομαι 1 1
MidPass:obj:Gen:νίκη 1

lemma:παρεκβαίνω 1 1
Act:obj:Gen:δίκαιος 1

lemma:καταβρίθω 1 1
Act:obj:Dat:μαλλός 1

lemma:καταφράζω 1 1
MidPass:obj:Acc:δίκη 1

lemma:ὀνοτάζω 1 1
Act:noobj:NA 1

lemma:κατοπάζω 1 1
Act:obj:Acc:αἰδώς 1

lemma:ὠνέομαι 1 1
MidPass:obj:Acc:κλῆρος 1

lemma:κερδαίνω 1 1
Act:obj:Acc:κακός 1

lemma:κωτίλλω 1 1
Act:obj:Acc:αἱμύλος 1

lemma:φέρβω 1 1
Act:obj:Acc:οἶκος 1

lemma:ἐγκαταλείπω 1 1
Act:obj:Acc:παῖς 1

lemma:βοωτέω 1 1
Act:noobj:NA 1

lemma:ἐπιμετρέω 1 1
Act:noobj:NA 1

lemma:διατεκμαίρομαι 1 2
Mid:obj:Acc:ὁ 1
Mid:iobj:Dat:ἄνθρωπος 1

lemma:ζητεύω 1 1
Act:obj:Acc:βίοτος 1

lemma:λυπέω 1 1
Act:noobj:NA 1

lemma:τητάομαι 1 1
MidPass:noobj:NA 1

lemma:ὀμβρέω 1 1
Act:obj:Acc:μετοπωρινός 1

lemma:ὑλοτομέω 1 1
Act:noobj:NA 1

lemma:χορτάζω 1 1
Act:obj:Acc:βοῦς 1

lemma:πληκτίζομαι 1 1
MidPass:obj:Dat:ἄλοχος 1

lemma:συναίνυμαι 1 1
MidPass:obj:Acc:τόξον 1

lemma:ἐπανατίθημι 1 1
Act:obj:Acc:σανίς 1

lemma:ὑποκλονέομαι 1 1
MidPass:obj:Dat:Ἀχιλλεύς 1

lemma:ἀπαείρω 1 2
MidPass:obj:Gen:πόλις 1
MidPass:obj:Acc:πεδίον 1

lemma:ἐπεῖδον 1 1
Act:obj:Acc:κακός 1

lemma:καταπτήσσω 1 1
Act:noobj:NA 1

lemma:ὑποφεύγω 1 1
Act:obj:Acc:ὁ 1

lemma:δείξω 1 1
Act:noobj:NA 1

lemma:περιτρέχω 1 1
Act:noobj:NA 1

lemma:καταλήθομαι 1 1
MidPass:obj:Gen:θνῄσκω 1

lemma:καταφέρω 1 1
Mid:obj:Acc:ἐγώ 1

lemma:καπύω 1 1
Act:obj:Acc:ψυχή 1

lemma:ἀπουρίζω 1 1
Act:obj:Acc:ἄρουρα 1

lemma:ὑπεμνήμυκε 1 1
Act:noobj:NA 1

lemma:ἀφοπλίζω 1 1
MidPass:obj:Acc:ἔντεα 1

lemma:ὀρεχθέω 1 1
Act:noobj:NA 1

lemma:ἀμφιχάσκω 1 1
Act:obj:Acc:ἐγώ 1

lemma:συμπλαταγέω 1 1
Act:noobj:NA 1

lemma:ἀποκείρω 1 1
Mid:obj:Acc:χαίτη 1

lemma:σκάλλω 1 1
Act:obj:Acc:χρώς 1

lemma:ὑπεκσῴζω 1 1
Act:obj:Acc:αὐτός 1

lemma:παρεκπροφεύγω 1 1
Act:obj:Acc:σύ 1

lemma:πλανάω 1 1
MidPass:noobj:NA 1

lemma:κεντέω 

{'κλείω': {'Act:noobj:NA': 1,
  'Act:obj:Acc:εἰμί': 2,
  'Act:obj:Acc:ἦθος': 1,
  'Act:obj:Acc:γένος': 1,
  'Act:obj:nocase:ὁ': 1,
  'Act:obj:Acc:σύ': 1},
 'ἐνέπω': {'Act:obj:Acc:Ζεύς': 1,
  'Act:obj:Dat:μῦθος': 1,
  'Act:noobj:NA': 4,
  'Act:obj:Acc:ὄνομα': 1,
  'Act:obj:Acc:ὄνειρος': 1,
  'Act:ccomp:Nom:ἄριστος': 1,
  'Act:iobj:Dat:ἐγώ': 11,
  'Act:obj:Dat:σφεῖς': 1,
  'Act:iobj:Dat:Ἀχιλλεύς': 1,
  'Act:obj:Acc:μῦθος': 3,
  'Act:obj:Acc:μῆτις': 1,
  'Act:ccomp:Nom:ἄξιος': 1,
  'Act:obj:Acc:οἶτος': 1,
  'Act:obj:Dat:φίλος': 2,
  'Act:ccomp:nocase:περιγίγνομαι': 2,
  'Act:iobj:Dat:σύ': 2,
  'Act:obj:Acc:νόστος': 1,
  'Act:obj:Acc:οὗτος': 1,
  'Act:obj:Dat:ἐγώ': 4,
  'Act:ccomp:nocase:ἀποκτείνω': 1,
  'Act:ccomp:nocase:ἄγω': 1,
  'Act:obj:Acc:θάνατος': 1,
  'Act:obj:Acc:κήρ': 1,
  'Act:obj:Acc:ἀνήρ': 1,
  'Act:obj:Acc:ὄλεθρος': 2,
  'Act:obj:Acc:νημερτής': 5,
  'Act:obj:Acc:ἀληθής': 1,
  'Act:obj:Acc:ὅδε': 1,
  'Act:obj:Acc:κληδών': 1,
  'Act:ccomp:nocase:οἴχομαι': 1,
  'Act:ccomp:nocas

In [104]:
verbobjsindex['εἶπον']['Act:ccomp:nocase:κελεύω']


['tlg0020.tlg001:sent2273935:12:tlg0020.tlg001:sent2273935:19',
 'tlg0012.tlg001:sent2276230:8:tlg0012.tlg001:sent2276230:14',
 'tlg0012.tlg001:sent2276377:10:tlg0012.tlg001:sent2276377:16',
 'tlg0012.tlg001:sent2276391:10:tlg0012.tlg001:sent2276391:16',
 'tlg0012.tlg001:sent2276458:11:tlg0012.tlg001:sent2276458:17',
 'tlg0012.tlg002:sent2187315:9:tlg0012.tlg002:sent2187315:15',
 'tlg0012.tlg002:sent2187410:10:tlg0012.tlg002:sent2187410:16',
 'tlg0012.tlg002:sent2191392:1:tlg0012.tlg002:sent2191392:7',
 'tlg0012.tlg002:sent2191439:2:tlg0012.tlg002:sent2191439:8',
 'tlg0012.tlg002:sent2190349:10:tlg0012.tlg002:sent2190349:16',
 'tlg0012.tlg002:sent2190658:10:tlg0012.tlg002:sent2190658:16']

In [97]:
curlem = 'ἡγεμονεύω'
for foo in sorted(verbargs[curlem],key=verbargs[curlem].get,reverse=True):
    print(foo,verbargs[curlem][foo])

KeyError: 'ἡγεμονεύω'

In [41]:
curlemma = 'χόλος'
curlemma = 'μῆνις'
curlemma = 'ἔχω'
curlemma = 'πέμπω'

print(len(lemmaindex[curlemma]))
deptot = 0
for foo in sorted(worddeprels[curlemma],key=worddeprels[curlemma].get,reverse=True):
    deptot = deptot + worddeprels[curlemma][foo]
    print(foo,worddeprels[curlemma][foo])
print(deptot,deptot/len(lemmaindex[curlemma]))

100
root 58
acl:relcl 20
ccomp 10
advcl 9
appos 1
parataxis 1
acl 1
100 1.0


In [32]:
worddeprels['χόλος']

{'obj': 40, 'nsubj': 23, 'obl': 2, 'obl:arg': 1, 'amod': 1}

In [14]:
re.search('\\bobj','obj')

<re.Match object; span=(0, 3), match='obj'>